## Document vector transforms on a Hindi (+dialects) corpus with the Rsemantic gem

The Rsemantic gem provides document vector search capabilities, supporting LSA and TF-IDF by default. As part of this work, we will use it's default transforms on a corpus of Hindi (and Hindi dialects) news reports scraped from the news website http://khabarlahariya.org . The Parser class of the gem has been modified to use a custom HindiStemmer class for stemming of Hindi data (specified by locale 'hi'). The HindiStemmer is a port to Ruby of http://research.variancia.com/hindi_stemmer/index.html with modifications per the extra dialects of Hindi in our data (suffix list has been modified, using material from https://books.google.co.in/books/about/A_Linguistic_Study_of_Bundeli.html?id=HMUrAAAAIAAJ as a guide). A custom stoplist has also been added to the gem's resource dir ('hi.stop') based on the most frequent words observed in the corpus.

The corpus scraped from khabarlahariya.org has been stored in the json format. First we import the corpus using the parse method from the 'json' gem:

In [3]:
# gem install json
require 'json'

file = IO.readlines('articlestream.json')
data = []
for line in file
  data << JSON.parse(line)
end
data.delete_at(0)


{"inputProperties"=>[{"type"=>"URL", "name"=>"webpage/url", "defaultValue"=>"http://khabarlahariya.org/?p=23132"}], "outputProperties"=>[{"type"=>"STRING", "name"=>"title"}, {"type"=>"STRING", "name"=>"byline"}, {"type"=>"STRING", "name"=>"article_text"}, {"type"=>"STRING", "name"=>"language"}, {"type"=>"STRING", "name"=>"location"}, {"type"=>"STRING", "name"=>"tags"}]}

Now we convert the data into an array of strings, which can be fed as input to the Rsemantic gem

In [4]:
data[1] # we can see the structure of our data

{"offset"=>0, "pageUrl"=>"http://khabarlahariya.org/?p=15100", "connectorGuid"=>"7cd98dc2-c187-4ed5-8455-3e424cc17f24", "results"=>[{"article_text"=>["जिला वाराणसी, ब्लाक, चिरईगाँव, हरहुअंा, गाँव गोपपुर, बड़ा लालपुर, अल्लोपुर। इहंा पर इ सबगाँव में बिजली नाहीं हव। कहीं पर लोग पचास साल से रहत हयन त कहीं पर लोग एक पीढ़ी से रहत हयन। गोपपुर के सन्तोष, मनोज अल्लोपुर के कुमारी देवी हीरामनी, राधेश्याम, बड़ा लालपुर, विश्वनाथ राम दीलिप के कहब हव कि हमने के इहंा पर रहत एतना दिन हो गएल हव। लेकिन अभहीं तक बिजली के कनेक्शन नाहीं हव। हमने दूसरे गाँव से बिजली जलावल जाला। तब सरकार भी हमने के तार काट के फेंक देला। जबकि हमने बिल भी जमा करल जला। अब त मिट्टी के तेल भी ढाई लीटर से दू लीटर हो गएल हव। एक महीना भी नाहीं चल पावला। बिजली विभाग के अधिकारी वी. पी. सिंह के कहब हव कि जहंा पर बिजली नाहीं हव। वो सब खातिर के करीब अस्सी करोड़ के योजना पास भयल हव। अभहीं इ कब तक चालू होई कुछ कहल नाहीं जा सकला।", "बिजली आउर पानी के लेके होत हव धरना", "जिला वाराणसी, लहुराबीर आजाद पार्क। बिधायक अजय राय के साथ लगभग एक सौ लोग 

In [5]:
data[1]["results"][0]["article_text"].to_s.gsub /\[?\"\]?/, ""

"जिला वाराणसी, ब्लाक, चिरईगाँव, हरहुअंा, गाँव गोपपुर, बड़ा लालपुर, अल्लोपुर। इहंा पर इ सबगाँव में बिजली नाहीं हव। कहीं पर लोग पचास साल से रहत हयन त कहीं पर लोग एक पीढ़ी से रहत हयन। गोपपुर के सन्तोष, मनोज अल्लोपुर के कुमारी देवी हीरामनी, राधेश्याम, बड़ा लालपुर, विश्वनाथ राम दीलिप के कहब हव कि हमने के इहंा पर रहत एतना दिन हो गएल हव। लेकिन अभहीं तक बिजली के कनेक्शन नाहीं हव। हमने दूसरे गाँव से बिजली जलावल जाला। तब सरकार भी हमने के तार काट के फेंक देला। जबकि हमने बिल भी जमा करल जला। अब त मिट्टी के तेल भी ढाई लीटर से दू लीटर हो गएल हव। एक महीना भी नाहीं चल पावला। बिजली विभाग के अधिकारी वी. पी. सिंह के कहब हव कि जहंा पर बिजली नाहीं हव। वो सब खातिर के करीब अस्सी करोड़ के योजना पास भयल हव। अभहीं इ कब तक चालू होई कुछ कहल नाहीं जा सकला।, बिजली आउर पानी के लेके होत हव धरना, जिला वाराणसी, लहुराबीर आजाद पार्क। बिधायक अजय राय के साथ लगभग एक सौ लोग धरना पर बइठल रहलन बिजली आउर पानी के मागं के लेके आउर ऐ लोगन के कहब हव कि अगर हमने के चैबीस घन्टा मे बिजली नाही आयल त हमने डी.एम कार्यालय में तोड फोड. करल 

In [6]:
documents = [] # a new empty container for our documents
# iterate through the data[] containerand concatenate the 'title' and 'article_text' and 'tags' (English) into a single string
data.each do |item|
  string = item["results"][0]["article_text"].to_s.gsub(/\[?\"\]?/, "") + item["results"][0]["title"].to_s + item["results"][0]["tags"].to_s.gsub("Tags:", '')
  documents += [string]
end

[{"offset"=>0, "pageUrl"=>"http://khabarlahariya.org/?p=22955", "connectorGuid"=>"7cd98dc2-c187-4ed5-8455-3e424cc17f24", "results"=>[{"article_text"=>["फैजाबाद मा अयोध्या के किनारे बसे गांवन मा हर साल मनईन का बाढ़ कै समस्या झेलै का पराथै। हर साल की तरह यहि बार भी बाढ़ आई अउर केतना घर बहि गये। मनई आपन सामान अउर जानवरन के साथे सुरक्षित स्थान पै जात अहैं।", "मूड़ाडीहा, पूरे चेतन, माझा सलेमपुर, पिपरी संग्रामपुर जैसे गंावन मा हर बार मनईन का बाढ़ कै समस्या झेलै का पराथै। बाढ़ के कटान मा हर बार मनई कै छप्पर नुमा घर बहि जाथै। मनई परेषान अहै कि हर बार यही समस्या। एक तौ कउनौ तरह छान छप्पर कै घर बनाय के गुजारा कीन जाथै। उहौ बासढ़ बहाय लै जायै। षासन-प्रषासन भी नाय कहत कि हर साल के समस्या से निजात दिलाय दियै। कहूं सुरक्षित स्थान पै रहै कै व्यवस्था कै दियै। का सरकार यकै सुविधा नाय दियत? वइसे तौ षासन-प्रषासन रासन के व्यवस्था हर बाढ़ मा करावाथै लकिन जब रहै कै जगह न रहे तौ मनई कवन मेर आपन गुजारा करे? बाढ़ के पहिले सुरक्षित स्थान पै जाए का कहि जाथै लकिन मनई जानवर अउर सामान लइके कहां जाए? अयोध्या बंधा पै

In [7]:
documents[0]

"फैजाबाद मा अयोध्या के किनारे बसे गांवन मा हर साल मनईन का बाढ़ कै समस्या झेलै का पराथै। हर साल की तरह यहि बार भी बाढ़ आई अउर केतना घर बहि गये। मनई आपन सामान अउर जानवरन के साथे सुरक्षित स्थान पै जात अहैं।, मूड़ाडीहा, पूरे चेतन, माझा सलेमपुर, पिपरी संग्रामपुर जैसे गंावन मा हर बार मनईन का बाढ़ कै समस्या झेलै का पराथै। बाढ़ के कटान मा हर बार मनई कै छप्पर नुमा घर बहि जाथै। मनई परेषान अहै कि हर बार यही समस्या। एक तौ कउनौ तरह छान छप्पर कै घर बनाय के गुजारा कीन जाथै। उहौ बासढ़ बहाय लै जायै। षासन-प्रषासन भी नाय कहत कि हर साल के समस्या से निजात दिलाय दियै। कहूं सुरक्षित स्थान पै रहै कै व्यवस्था कै दियै। का सरकार यकै सुविधा नाय दियत? वइसे तौ षासन-प्रषासन रासन के व्यवस्था हर बाढ़ मा करावाथै लकिन जब रहै कै जगह न रहे तौ मनई कवन मेर आपन गुजारा करे? बाढ़ के पहिले सुरक्षित स्थान पै जाए का कहि जाथै लकिन मनई जानवर अउर सामान लइके कहां जाए? अयोध्या बंधा पै घास फूस मा कब तक गुजारा होये? लकिन मजबूरी मा आपन आषियाना छोड़ै का पराथै।सुरक्षित स्थान पै जाय का मजबूर displacement, faizabad, floods, relocation"

We are ready to feed our data to the Rsemantic gem. 

In [8]:
require './rsemantic/lib/rsemantic.rb'

true

In [31]:
search = RSemantic::Search.new(documents[0..500], options = {:locale => 'hi', :transforms => [:LSA]})

#<RSemantic::Search:0x007fd4cad936a8 @builder=#<RSemantic::VectorSpace::Builder:0x007fd4cad935b8 @parser=#<RSemantic::Parser:0x007fd4cad93568 @filter_stop_words=true, @stem_words=true, @locale="hi", @stopwords=#<Set: {"के", "का", "एक", "में", "की", "है", "यह", "और", "से", "हैं", "को", "पर", "इस", "होता", "कि", "जो", "कर", "मे", "गया", "करने", "किया", "लिये", "अपने", "ने", "बनी", "नहीं", "तो", "ही", "या", "एवं", "दिया", "हो", "इसका", "था", "द्वारा", "हुआ", "तक", "साथ", "करना", "वाले", "बाद", "लिए", "आप", "कुछ", "सकते", "किसी", "ये", "इसके", "सबसे", "इसमें", "थे", "दो", "होने", "वह", "वे", "करते", "बहुत", "कहा", "वर्ग", "कई", "करें", "होती", "अपनी", "उनके", "थी", "यदि", "हुई", "जा", "ना", "इसे", "कहते", "जब", "होते", "कोई", "हुए", "व", "न", "अभी", "जैसे", "सभी", "करता", "उनकी", "तरह", "उस", "आदि", "कुल", "एस", "रहा", "इसकी", "सकता", "रहे", "उनका", "इसी", "रखें", "अपना", "पे", "उसके", "तथा", "भी", "परंतु", "इन", "कम", "लेकिन", "यहाँ", "दूर", "उत्तर", "पूरे", "गये", "तुम", "मै", "यहां", "ह

In [42]:
search.related(0).each_with_index {|w, i| puts "#{i} : #{w}" }

0 : 0.999999999999962
1 : 0.033775792241125126
2 : 0.11677292564474147
3 : 0.006842441276844405
4 : 0.009526496094254688
5 : 0.04776983305791959
6 : 0.007250190581631857
7 : 0.06925230790597171
8 : 0.02111271809821061
9 : 0.11143168419546903
10 : 0.0722335980867786
11 : 0.12012439625246457
12 : -0.0014701586978581372
13 : 0.03930378198517828
14 : -0.04193176164798371
15 : 0.06076011640864434
16 : -5.096926043809397e-05
17 : 0.27034576284453266
18 : 0.08627453217509881
19 : 0.04917345121777306
20 : 0.05045846931803999
21 : 0.0006876505852945944
22 : 1.4380323449110274e-05
23 : -0.001141587488889174
24 : 0.02417940114459028
25 : 0.0034837486068985315
26 : 0.039254948303168065
27 : 0.0082866993220404
28 : -0.006034754872202431
29 : 0.136805594215379
30 : 0.06811631762097234
31 : 0.030614457891054145
32 : 0.09693016097778137
33 : -0.002009700627282645
34 : 0.07337167347636567
35 : 0.09028432935305275
36 : -4.7178171838941745e-05
37 : -0.009882085028519056
38 : 0.07042974653803404
39 : 0.00

[0.999999999999962, 0.033775792241125126, 0.11677292564474147, 0.006842441276844405, 0.009526496094254688, 0.04776983305791959, 0.007250190581631857, 0.06925230790597171, 0.02111271809821061, 0.11143168419546903, 0.0722335980867786, 0.12012439625246457, -0.0014701586978581372, 0.03930378198517828, -0.04193176164798371, 0.06076011640864434, -5.096926043809397e-05, 0.27034576284453266, 0.08627453217509881, 0.04917345121777306, 0.05045846931803999, 0.0006876505852945944, 1.4380323449110274e-05, -0.001141587488889174, 0.02417940114459028, 0.0034837486068985315, 0.039254948303168065, 0.0082866993220404, -0.006034754872202431, 0.136805594215379, 0.06811631762097234, 0.030614457891054145, 0.09693016097778137, -0.002009700627282645, 0.07337167347636567, 0.09028432935305275, -4.7178171838941745e-05, -0.009882085028519056, 0.07042974653803404, 0.0037095059323175887, 0.05482930421825451, 0.03982762102756468, 0.19035420387639138, 0.050966944315330664, 0.04501013327550919, 0.05577079101088634, 0.06

In [35]:
puts search.search([""])

[-1.4963856893058409e-05, -7.426763832028741e-05, 0.00024897395415728735, -4.4527879244495945e-05, -0.01973178713042383, -0.009945178621658798, -7.465448369340837e-05, -2.3002278996380202e-05, -0.0003282908142545429, 3.5975011752738065e-05, 2.6797511700324393e-05, 3.9232647105955476e-05, -0.0004058576288137196, -3.2727521442483864e-05, -0.0005866652333935169, -1.1415758390140508e-05, 4.502290235090338e-05, -6.0822766593418e-05, -0.00016780367647786852, 0.0002995122223318775, 1.4724580314279567e-05, -0.012780217499817349, -8.316640733624021e-06, -0.007090828337218415, 0.00010115675181478961, -7.207204911137072e-05, -0.0001529125558066208, 0.0004460083314554986, -0.00013382358565928762, -0.00011728136149449965, -0.0003705097569721632, -8.141478515243724e-05, 8.833525164556433e-05, -0.013802838371628394, -0.00034062996419671255, 2.5152016104752296e-05, -0.0011515056970313575, -0.00016098852736415927, -1.707844144320524e-05, -0.01753710872120144, -1.433380879920726e-05, 0.01385669747182168

documents[0] and [48] have a similarity weight of 0.68, we can compare them below and see that they are both indeed pertaining to a similar topic. 

In [48]:
documents[0]

"फैजाबाद मा अयोध्या के किनारे बसे गांवन मा हर साल मनईन का बाढ़ कै समस्या झेलै का पराथै। हर साल की तरह यहि बार भी बाढ़ आई अउर केतना घर बहि गये। मनई आपन सामान अउर जानवरन के साथे सुरक्षित स्थान पै जात अहैं।, मूड़ाडीहा, पूरे चेतन, माझा सलेमपुर, पिपरी संग्रामपुर जैसे गंावन मा हर बार मनईन का बाढ़ कै समस्या झेलै का पराथै। बाढ़ के कटान मा हर बार मनई कै छप्पर नुमा घर बहि जाथै। मनई परेषान अहै कि हर बार यही समस्या। एक तौ कउनौ तरह छान छप्पर कै घर बनाय के गुजारा कीन जाथै। उहौ बासढ़ बहाय लै जायै। षासन-प्रषासन भी नाय कहत कि हर साल के समस्या से निजात दिलाय दियै। कहूं सुरक्षित स्थान पै रहै कै व्यवस्था कै दियै। का सरकार यकै सुविधा नाय दियत? वइसे तौ षासन-प्रषासन रासन के व्यवस्था हर बाढ़ मा करावाथै लकिन जब रहै कै जगह न रहे तौ मनई कवन मेर आपन गुजारा करे? बाढ़ के पहिले सुरक्षित स्थान पै जाए का कहि जाथै लकिन मनई जानवर अउर सामान लइके कहां जाए? अयोध्या बंधा पै घास फूस मा कब तक गुजारा होये? लकिन मजबूरी मा आपन आषियाना छोड़ै का पराथै।सुरक्षित स्थान पै जाय का मजबूर displacement, faizabad, floods, relocation"

In [47]:
documents[48]

"जिला फैजाबाद, ब्लाक पूराबाजार, गंाव मूड़ाडीहा, पूरे चेतन, माझा सलेमपुर, पिपरी संगा्रम, उरदहवा बस्ती। हिंआ के लगभग दसन परिवार कै मनई बाढ़ के कारण आपन घर छोड़ के जानवरन के साथे सुरक्षित जगह पै पलायन करिन। बिल्वहरिघाट अयोध्या बंधा पै घास-फूस मा तिरपाल डारि के रहै कै जगह बनाइन।, सलेमपुर गांव कै पारसनाथ, धर्मराज बताइन कि हमार घर कटान के कगार पै बाय। यही से हमरे सब घर छोड़ के तिरपाल डाय के रहै का ठिकाना बनायन। सब समान उठाय लावत हई नाहीं तौ डूब जाये। हमार घर छप्पर कै बाय जब बाढ़ आवाथै तौ पन्नी तान के रहे का पड़ाथै। पुराना छप्पर डूब जाथै। हर बार इहै समस्या झेलै का पराथै।, प्रधान तेज बहादुर निषाद बताइन कि पारसनाथ, धर्मराज, जगदीष, रामवचन, गुरू प्रसाद अउर नैजी निषाद कै घर कटान के कगार पै बाय। लकिन हमसे जवन होय सके हम उनकै मदद करब।, एस.डी.एम. अमित सिंह बताइन कि पूरे ब्लाक के प्रभावित गांवन कै निरीक्षण कीन गै। गंाव के मनई का सुरक्षित जगह पै रहै का सलाह देहे हई। राजस्व कर्मियन का निर्देष दिहे बाटेन कि पूरी सुविधा ग्रामीणन का देवावा जाए।बाढ़ के खतरा से परेषान मनई faizabad, floods"